In [ ]:
from roboflow import Roboflow

rf = Roboflow(api_key="LqD8Cs4OsoK8seO3CPkf")  # Make sure your API key is correct
project = rf.workspace("car-damage-detection-wjnwh").project("car-damage-detection-krsix")
version = project.version(2)
dataset = version.download("coco")  # Downloading in COCO format


In [1]:
from detectron2.data.datasets import register_coco_instances
from detectron2.config import get_cfg
from detectron2 import model_zoo
import os
from detectron2.engine import DefaultTrainer

dataset_path = "car-damage-detection-2"  # Update with your correct dataset path

# ✅ Register COCO dataset for instance segmentation
register_coco_instances("car_damage_train", {}, 
                        f"{dataset_path}/train/_annotations.coco.json", 
                        f"{dataset_path}/train")

register_coco_instances("car_damage_val", {}, 
                        f"{dataset_path}/valid/_annotations.coco.json", 
                        f"{dataset_path}/valid")

register_coco_instances("car_damage_test", {}, 
                        f"{dataset_path}/test/_annotations.coco.json", 
                        f"{dataset_path}/test")

# ✅ Load configuration for Mask R-CNN
cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-Detection/faster_rcnn_R_50_FPN_3x.yaml"))

cfg.DATASETS.TRAIN = ("car_damage_train",)
cfg.DATASETS.TEST = ("car_damage_val",)
cfg.DATALOADER.NUM_WORKERS = 4
cfg.INPUT.MASK_FORMAT = "polygon"  # ✅ This ensures segmentation masks are in polygon format

cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url("COCO-Detection/faster_rcnn_R_50_FPN_3x.yaml")  
cfg.SOLVER.IMS_PER_BATCH = 2
cfg.SOLVER.BASE_LR = 0.00025  
cfg.SOLVER.MAX_ITER = 6559  # Adjust based on dataset size
cfg.MODEL.ROI_HEADS.BATCH_SIZE_PER_IMAGE = 512  
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 47  # Update this based on your dataset

cfg.OUTPUT_DIR = "./output"
os.makedirs(cfg.OUTPUT_DIR, exist_ok=True)

# Train the model
trainer = DefaultTrainer(cfg)
trainer.resume_or_load(resume=False)
trainer.train()


[03/11 13:13:23 d2.engine.defaults]: Model:
GeneralizedRCNN(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
      (res

Skip loading parameter 'roi_heads.box_predictor.cls_score.weight' to the model due to incompatible shapes: (81, 1024) in the checkpoint but (48, 1024) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.cls_score.bias' to the model due to incompatible shapes: (81,) in the checkpoint but (48,) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.bbox_pred.weight' to the model due to incompatible shapes: (320, 1024) in the checkpoint but (188, 1024) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.bbox_pred.bias' to the model due to incompatible shapes: (320,) in the checkpoint but (188,) in the model! You might want to double check if this is expected.
Some model parameters or buffers are not found in the checkpoint:
roi_heads.box_predictor.bbox_pred.{bias, weight}
roi_heads.box_predictor.cls_score.{bi

[03/11 13:13:24 d2.engine.train_loop]: Starting training from iteration 0


/home/mcw/miniconda3/envs/rohithk/lib/python3.12/site-packages/torch/functional.py:539: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at /pytorch/aten/src/ATen/native/TensorShape.cpp:3637.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


[03/11 13:13:39 d2.utils.events]:  eta: 1:03:23  iter: 19  total_loss: 4.141  loss_cls: 3.863  loss_box_reg: 0.165  loss_rpn_cls: 0.0805  loss_rpn_loc: 0.01811    time: 0.5796  last_time: 0.5409  data_time: 0.0257  last_data_time: 0.0174   lr: 4.9953e-06  max_mem: 1739M


2025-03-11 13:13:40.846796: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1741679021.006687 1797043 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1741679021.033001 1797043 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-03-11 13:13:41.327110: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


[03/11 13:14:00 d2.utils.events]:  eta: 1:01:52  iter: 39  total_loss: 3.919  loss_cls: 3.684  loss_box_reg: 0.1183  loss_rpn_cls: 0.06942  loss_rpn_loc: 0.01833    time: 0.5740  last_time: 0.5861  data_time: 0.0155  last_data_time: 0.0183   lr: 9.9902e-06  max_mem: 1739M
[03/11 13:14:11 d2.utils.events]:  eta: 1:01:53  iter: 59  total_loss: 3.615  loss_cls: 3.289  loss_box_reg: 0.128  loss_rpn_cls: 0.07853  loss_rpn_loc: 0.01824    time: 0.5722  last_time: 0.6104  data_time: 0.0132  last_data_time: 0.0031   lr: 1.4985e-05  max_mem: 1739M
[03/11 13:14:22 d2.utils.events]:  eta: 1:01:29  iter: 79  total_loss: 2.856  loss_cls: 2.648  loss_box_reg: 0.1373  loss_rpn_cls: 0.03618  loss_rpn_loc: 0.01702    time: 0.5717  last_time: 0.6092  data_time: 0.0153  last_data_time: 0.0145   lr: 1.998e-05  max_mem: 1740M
[03/11 13:14:34 d2.utils.events]:  eta: 1:00:53  iter: 99  total_loss: 2.16  loss_cls: 1.83  loss_box_reg: 0.1615  loss_rpn_cls: 0.08883  loss_rpn_loc: 0.02448    time: 0.5693  last_t

In [4]:
from detectron2.evaluation import COCOEvaluator, inference_on_dataset
from detectron2.data import build_detection_test_loader

evaluator = COCOEvaluator("car_damage_val", cfg, False, output_dir="./output/")
val_loader = build_detection_test_loader(cfg, "car_damage_val")
print(inference_on_dataset(trainer.model, val_loader, evaluator))


WARNING [03/11 14:16:24 d2.evaluation.coco_evaluation]: COCO Evaluator instantiated using config, this is deprecated behavior. Please pass in explicit arguments instead.
WARNING [03/11 14:16:24 d2.data.datasets.coco]: 
Category ids in annotations are not in [1, #categories]! We'll apply a mapping for you.

[03/11 14:16:24 d2.data.datasets.coco]: Loaded 1335 images in COCO format from car-damage-detection-2/valid/_annotations.coco.json
[03/11 14:16:24 d2.data.dataset_mapper]: [DatasetMapper] Augmentations used in inference: [ResizeShortestEdge(short_edge_length=(800, 800), max_size=1333, sample_style='choice')]
[03/11 14:16:24 d2.data.common]: Serializing the dataset using: <class 'detectron2.data.common._TorchSerializedList'>
[03/11 14:16:24 d2.data.common]: Serializing 1335 elements to byte tensors and concatenating them all ...
[03/11 14:16:24 d2.data.common]: Serialized dataset takes 1.72 MiB
[03/11 14:16:24 d2.evaluation.evaluator]: Start inference on 1335 batches
[03/11 14:16:26 d

In [8]:
import cv2
from detectron2.engine import DefaultPredictor
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog

cfg.MODEL.WEIGHTS = "./output/model_final.pth"
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.5
predictor = DefaultPredictor(cfg)

image_path = f"{dataset_path}/test/000269_jpg.rf.df40944b29ad5d9b144b86af2baef5b8.jpg" 
image = cv2.imread(image_path)
outputs = predictor(image)

v = Visualizer(image[:, :, ::-1], MetadataCatalog.get("car_damage_train"), scale=0.8)
pred_classes = outputs["instances"].pred_classes.tolist()  

metadata = MetadataCatalog.get("car_damage_train")
class_names = metadata.get("thing_classes", None)

if class_names:
    pred_labels = [class_names[i] for i in pred_classes] 
else:
    pred_labels = pred_classes

print("Predicted Classes:", pred_labels)

v = v.draw_instance_predictions(outputs["instances"].to("cpu"))
cv2.imwrite("output.jpg", v.get_image()[:, :, ::-1]) 
cv2.waitKey(0)


[03/11 14:21:32 d2.checkpoint.detection_checkpoint]: [DetectionCheckpointer] Loading from ./output/model_final.pth ...
Predicted Classes: ['shattered_glass']


error: OpenCV(4.10.0) /io/opencv/modules/highgui/src/window.cpp:1367: error: (-2:Unspecified error) The function is not implemented. Rebuild the library with Windows, GTK+ 2.x or Cocoa support. If you are on Ubuntu or Debian, install libgtk2.0-dev and pkg-config, then re-run cmake or configure script in function 'cvWaitKey'
